In [19]:
# Models
from sklearn.svm import LinearSVC #SVC
from sklearn.ensemble import RandomForestClassifier
from sklearn.linear_model import SGDClassifier
# Other Packages
import pandas as pd
import numpy as np
from sklearn.metrics import classification_report, confusion_matrix
from sklearn.model_selection import train_test_split
from sklearn.impute import SimpleImputer
from sklearn.externals import joblib
import random
from timeit import default_timer as timer
import matplotlib.pyplot as plt
import seaborn as sns
from imblearn.over_sampling import SMOTE
# Display settings
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', 100)

In [2]:
# Label mappings
label_group_dict = { 0: 0,
                     1: 'chapter',
                     2: 'company',
                     3: 'directive',
                     4: 'signal',
                     5: 'subchapter',
                     6: 'usecase_con',
                     7: 'usecase_pro',
                     8: 'version'}

date_dict = {0: 0,
             1: 'oldversiondate',
             2: 'validdate',
             3: 'printdate',
             4: 'revisiondate'}

In [3]:
def set_feature_rng (data):
    # Ranges Feature
    colidx = data.columns.get_loc
    # No window
    r_paper = np.r_[colidx('word.is.lower'):colidx('word.is.stop')]
    r_own = np.r_[colidx('word.is.bold'):colidx('is.page.3')]
    r_own_date_spe = np.r_[colidx('word.is.print.date.trigger'):colidx('word.is.oldversion.date.trigger')]
    r_own_date_full = np.r_[r_own, r_own_date_spe]
    r_web = np.r_[colidx('0'):colidx('299')]

    feature_selection = [('Paper', r_paper),
                        ('Own', r_own),
                        ('Wordembedding', r_web),
                        ('Own+Paper', np.r_[r_own, r_paper]),
                        ('Own+Wordembedding', np.r_[r_own, r_web]),
                        ('Paper+Wordembedding', np.r_[r_paper, r_web]),
                        ('Own+Paper+Wordembedding', np.r_[r_own, r_paper, r_web]),
                        ('date_Paper', r_paper),
                        ('date_Own_std', r_own),
                        ('date_Own_spe', r_own_date_spe),
                        ('date_Own_full', r_own_date_full),
                        ('date_Own_full+Paper', np.r_[r_own_date_full, r_paper]),
                        ('date_Own_full+Wordembedding', np.r_[r_own_date_full, r_web]),
                        ('date_Paper+Wordembedding', np.r_[r_paper, r_web]),
                        ('date_Own_full+Paper+Wordembedding', np.r_[r_own_date_full, r_paper, r_web]),
                        ]

    return feature_selection

In [4]:
def set_feature_rng_w (data):
    # Ranges Feature
    colidx = data.columns.get_loc

    # With window
    r_paper_w = np.r_[colidx('word.is.lower'):colidx('+6_word.is.stop')]
    r_own_w = np.r_[colidx('word.is.bold'):colidx('+6_is.page.3')]
    r_own_date_spe_w = np.r_[colidx('word.is.print.date.trigger'):colidx('+6_word.is.oldversion.date.trigger')]
    r_own_date_full_w = np.r_[r_own_w, r_own_date_spe_w]
    r_web_w = np.r_[colidx('0'):colidx('+1_299')]

    feature_selection_w = [('Paper', r_paper_w),
                        ('Own', r_own_w),
                        ('Wordembedding', r_web_w),
                        ('Own+Paper', np.r_[r_own_w, r_paper_w]),
                        ('Own+Wordembedding', np.r_[r_own_w, r_web_w]),
                        ('Paper+Wordembedding', np.r_[r_paper_w, r_web_w]),
                        ('Own+Paper+Wordembedding', np.r_[r_own_w, r_paper_w, r_web_w]),
                        ('date_Paper', r_paper_w),
                        ('date_Own_std', r_own_w),
                        ('date_Own_spe', r_own_date_spe_w),
                        ('date_Own_full', r_own_date_full_w),
                        ('date_Own_full+Paper', np.r_[r_own_date_full_w, r_paper_w]),
                        ('date_Own_full+Wordembedding', np.r_[r_own_date_full_w, r_web_w]),
                        ('date_Paper+Wordembedding', np.r_[r_paper_w, r_web_w]),
                        ('date_Own_full+Paper+Wordembedding', np.r_[r_own_date_full_w, r_paper_w, r_web_w]),
                        ]
    
    return feature_selection_w

In [13]:
def prepare_data (data, sample_size): #max sample_size = 527
    # Create Dataframe of unique docs to use sample function from pandas with random state
    docs = pd.DataFrame(data.doc.unique())
    random_docs = docs[0].sample(n=sample_size, random_state=1).values.tolist()
    data_sample = data[data['doc'].isin(random_docs)]
    data_sample1 = data_sample.loc[:, 'doc':'chem']
    data_sample2 = data_sample.loc[:, 'word.is.lower':data.iloc[:,-1].name]

    # Replace missing values
    data_sample2 = data_sample2.fillna(data_sample2.mode().iloc[0])
    data_sample = pd.concat([data_sample1, data_sample2], axis=1, sort=False)

    # Split random_docs in test and training sets
    docs_train, docs_test = train_test_split(random_docs, random_state=1)

    # Split random_data in test and training sets
    train, test = data_sample[data_sample['doc'].isin(docs_train)], data_sample[data_sample['doc'].isin(docs_test)]
    
    return train, test

In [6]:
def train_model (feat,lab):
    print ('   **************************Label:' + lab + '**************************')
    # Separate random_data training/test split in features and labels
    x_train = train.iloc[:, feat[1]]
    x_test = test.iloc[:, feat[1]]
    y_train = train.loc[:, lab]
    y_test = test.loc[:, lab]

    # Balance classes
    #smote = SMOTE('minority')
    #x_sm, y_sm = smote.fit_sample(x_train, y_train)

    # training
    start = timer()
    clf = RandomForestClassifier(n_estimators=25)
    clf.fit (x_train, y_train)
    #clf.fit(x_sm, y_sm)
    y_pred = clf.predict(x_test)
    end = timer()
    print('Seconds for training:', end - start)

    # scores
    print(classification_report(y_pred=y_pred, y_true=y_test))

    # Output a pickle file for the model
    joblib.dump(clf, './models/'+ feat[0] + '_' + lab + '.pkl')

In [7]:
def start_training (feature_selection, lab):
    for feat in feature_selection:
        print ('*******************************Features:' + feat[0] + '*******************************')
    
        if feat[0].startswith('date'):
            train_model(feat,'date')
        else:
            for l in lab:
                train_model(feat,l)

In [8]:
data = pd.read_pickle('data_model_allfeatw13_4_web3.pkl')

In [9]:
data

doc  Page                   word      label  label_dum  \
0       001_sd.pdf   1.0  Sicherheitsdatenblatt        NaN         -1   
1       001_sd.pdf   1.0                  gemäß        NaN         -1   
2       001_sd.pdf   1.0          EU-Verordnung        NaN         -1   
3       001_sd.pdf   1.0               2015/830  directive        101   
4       001_sd.pdf   1.0                  Seite        NaN         -1   
...            ...   ...                    ...        ...        ...   
537964  741_sd.pdf   3.0                  Seite        NaN         -1   
537965  741_sd.pdf   3.0                      4        NaN         -1   
537966  741_sd.pdf   3.0                      )        NaN         -1   
537967  741_sd.pdf   3.0                 46.0.2        NaN         -1   
537968  741_sd.pdf   3.0                     DE        NaN         -1   

        label_group  chapter  subchapter  version  directive  signal  company  \
0                 0      0.0         0.0      0.0        0.0     0.0      0.0   
1                 0      0.0         0.0      0.0        0.0     0.0      0.0   
2                 0      0.0         0.0      0.0        0.0     0.0      0.0   
3                 3      0.0         0.0      0.0        1.0     0.0      0.0   
4                 0      0.0         0.0      0.0        0.0     0.0      0.0   
...             ...      ...         ...      ...        ...     ...      ...   
537964            0      0.0         0.0      0.0        0.0     0.0      0.0   
537965            0      0.0         0.0      0.0        0.0     0.0      0.0   
537966            0      0.0         0.0      0.0        0.0     0.0      0.0   
537967            0      0.0         0.0      0.0        0.0     0.0      0.0   
537968            0      0.0         0.0      0.0        0.0     0.0      0.0   

        usecase  usecase_con  usecase_pro  date  date_oldversiondate  \
0           0.0          0.0          0.0   0.0                  0.0   
1           0.0          0.0          0.0   0.0                  0.0   
2           0.0          0.0          0.0   0.0                  0.0   
3           0.0          0.0          0.0   0.0                  0.0   
4           0.0          0.0          0.0   0.0                  0.0   
...         ...          ...          ...   ...                  ...   
537964      0.0          0.0          0.0   0.0                  0.0   
537965      0.0          0.0          0.0   0.0                  0.0   
537966      0.0          0.0          0.0   0.0                  0.0   
537967      0.0          0.0          0.0   0.0                  0.0   
537968      0.0          0.0          0.0   0.0                  0.0   

        date_printdate  date_revisiondate  date_validdate  chem  \
0                  0.0                0.0             0.0   0.0   
1                  0.0                0.0             0.0   0.0   
2                  0.0                0.0             0.0   0.0   
3                  0.0                0.0             0.0   0.0   
4                  0.0                0.0             0.0   0.0   
...                ...                ...             ...   ...   
537964             0.0                0.0             0.0   0.0   
537965             0.0                0.0             0.0   0.0   
537966             0.0                0.0             0.0   0.0   
537967             0.0                0.0             0.0   0.0   
537968             0.0                0.0             0.0   0.0   

        word.is.lower  word.is.upper  word.is.mixed.case  word.is.digit  \
0                 0.0            0.0                 1.0            0.0   
1                 1.0            1.0                 0.0            0.0   
2                 0.0            0.0                 1.0            0.0   
3                 0.0            0.0                 1.0            0.0   
4                 0.0            0.0                 1.0            0.0   
...               ...            ...         

In [12]:
# load the model from disk
loaded_model = joblib.load('./models/Own+Paper+Wordembedding_label_group.pkl')

In [14]:
train, test = prepare_data(data, 527)

colidx = data.columns.get_loc

r_paper_w = np.r_[colidx('word.is.lower'):colidx('+6_word.is.stop')]
r_own_w = np.r_[colidx('word.is.bold'):colidx('+6_is.page.3')]
r_own_date_spe_w = np.r_[colidx('word.is.print.date.trigger'):colidx('+6_word.is.oldversion.date.trigger')]
r_own_date_full_w = np.r_[r_own_w, r_own_date_spe_w]
r_web_w = np.r_[colidx('0'):colidx('+1_299')]

In [16]:
a = data.iloc[:, np.r_[colidx('word.is.lower'):colidx('+6_word.is.stop')]]
a =1

In [17]:
selection = np.r_[r_own_w, r_paper_w, r_web_w]

In [20]:
#x_train = train.iloc[:, selection]
x_test = test.iloc[:, selection]
#y_train = train.loc[:, lab]
y_test = test.loc[:, 'label_group']

a = loaded_model.predict(x_test)
a = pd.DataFrame(a)

b = pd.concat([test['word'],y_test, a], axis = 1, sort = False,  ignore_index=False)
b[(b['label_group'] !=0)]

word  label_group    0
3                    2015/830          3.0  3.0
34                  ABSCHNITT          1.0  1.0
35                          1          1.0  1.0
36                          :          1.0  1.0
37                Bezeichnung          1.0  1.0
38                        des          1.0  1.0
39                     Stoffs          1.0  1.0
40                        bzw          1.0  1.0
41                          .          1.0  1.0
42                        des          1.0  1.0
43                   Gemischs          1.0  1.0
44                        und          1.0  1.0
45                        des          1.0  1.0
46               Unternehmens          1.0  1.0
47                        1.1          5.0  5.0
48       Produktidentifikator          5.0  5.0
71                        1.2          5.0  5.0
72                  Relevante          5.0  5.0
73             identifizierte          5.0  5.0
74               Verwendungen          5.0  5.0
75                        des          5.0  5.0
76                     Stoffs          5.0  5.0
77                       oder          5.0  5.0
78                   Gemischs          5.0  5.0
79                        und          5.0  5.0
80               Verwendungen          5.0  5.0
81                          ,          5.0  5.0
82                        von          5.0  5.0
83                      denen          5.0  5.0
84                  abgeraten          5.0  5.0
85                       wird          5.0  5.0
89          Gartenteichbedarf          6.0  6.0
90                        1.3          5.0  5.0
91               Einzelheiten          5.0  5.0
92                        zum          5.0  5.0
93                Lieferanten          5.0  5.0
94                          ,          5.0  5.0
95                        der          5.0  5.0
96                        das          5.0  5.0
97      Sicherheitsdatenblatt          5.0  5.0
98               bereitstellt          5.0  5.0
106                      Söll          2.0  2.0
107                      GmbH          2.0  2.0
108                         ,          2.0  2.0
147                       1.4          5.0  5.0
148              Notrufnummer          5.0  5.0
200                 ABSCHNITT          1.0  1.0
201                         2          1.0  1.0
202                         :          1.0  1.0
203                  Mögliche          1.0  1.0
...                       ...          ...  ...
532524                      :          1.0  NaN
532525              Maßnahmen          1.0  NaN
532526                    bei          1.0  NaN
532527       unbeabsichtigter          1.0  NaN
532528            Freisetzung          1.0  NaN
532581                      8          8.0  NaN
532659              ABSCHNITT          1.0  NaN
532660                      7          1.0  NaN
532661                      :          1.0  NaN
532662             Handhabung          1.0  NaN
532663                    und          1.0  NaN
532664               Lagerung          1.0  NaN
532756              ABSCHNITT          1.0  NaN
532757                      8          1.0  NaN
532758                      :          1.0  NaN
532759             Begrenzung          1.0  NaN
532760                    und          1.0  NaN
532761            Überwachung          1.0  NaN
532762                    der          1.0  NaN
532763             Exposition          1.0  NaN
532764                      /          1.0  NaN
532765            Persönliche          1.0  NaN
532766     Schutzausrüstungen          1.0  NaN
535692                    vom          8.0  NaN
535697                    7.2          8.0  NaN
535738                  Keine          6.0  NaN
535739                    bei          6.0  NaN
535740     bestimmungsgemäßer          6.0  NaN
535741           Verarbeitung          6.0  NaN
535742                      .          6.0  NaN
535743            Technisches          6.0  NaN
535744              Merkblatt          6.

# Train/test models

In [ ]:
print ('***************************************NO_WINDOW***************************************')
data = pd.read_pickle('data_model_allfeatw13_4_web.pkl')
data

In [ ]:
feature_selection = set_feature_rng(data)
train, test = prepare_data(data, 527)
start_training(feature_selection, ['label_group', 'chem', 'date'])

In [10]:
print ('***************************************WINDOW***************************************')
data = pd.read_pickle('data_model_allfeatw13_4_web3.pkl')
data

***************************************WINDOW***************************************


doc  Page                                    word  \
0       001_sd.pdf   1.0                   Sicherheitsdatenblatt   
1       001_sd.pdf   1.0                                   gemäß   
2       001_sd.pdf   1.0                           EU-Verordnung   
3       001_sd.pdf   1.0                                2015/830   
4       001_sd.pdf   1.0                                   Seite   
5       001_sd.pdf   1.0                                       1   
6       001_sd.pdf   1.0                                     von   
7       001_sd.pdf   1.0                                       6   
8       001_sd.pdf   1.0                       Ausstellungsdatum   
9       001_sd.pdf   1.0                                       :   
10      001_sd.pdf   1.0                              10.11.2017   
11      001_sd.pdf   1.0                                  Ersatz   
12      001_sd.pdf   1.0                                     für   
13      001_sd.pdf   1.0                                     das   
14      001_sd.pdf   1.0                              Datenblatt   
15      001_sd.pdf   1.0                                     von   
16      001_sd.pdf   1.0                                       :   
17      001_sd.pdf   1.0                              20.11.2015   
18      001_sd.pdf   1.0                                     "*"   
19      001_sd.pdf   1.0                              Änderungen   
20      001_sd.pdf   1.0                               gegenüber   
21      001_sd.pdf   1.0                               Vorläufer   
22      001_sd.pdf   1.0                                       ,   
23      001_sd.pdf   1.0                                     n.a   
24      001_sd.pdf   1.0                                       .   
25      001_sd.pdf   1.0                                       =   
26      001_sd.pdf   1.0                                   nicht   
27      001_sd.pdf   1.0                               anwendbar   
28      001_sd.pdf   1.0                                       ,   
29      001_sd.pdf   1.0                                     n.v   
30      001_sd.pdf   1.0                                       .   
31      001_sd.pdf   1.0                                       =   
32      001_sd.pdf   1.0                                   nicht   
33      001_sd.pdf   1.0                               verfügbar   
34      001_sd.pdf   1.0                               ABSCHNITT   
35      001_sd.pdf   1.0                                       1   
36      001_sd.pdf   1.0                                       :   
37      001_sd.pdf   1.0                             Bezeichnung   
38      001_sd.pdf   1.0                                     des   
39      001_sd.pdf   1.0                                  Stoffs   
40      001_sd.pdf   1.0                                     bzw   
41      001_sd.pdf   1.0                                       .   
42      001_sd.pdf   1.0                                     des   
43      001_sd.pdf   1.0                                Gemischs   
44      001_sd.pdf   1.0                                     und   
45      001_sd.pdf   1.0                                     des   
46      001_sd.pdf   1.0                            Unternehmens   
47      001_sd.pdf   1.0                                     1.1   
48      001_sd.pdf   1.0                    Produktidentifikator   
49      001_sd.pdf   1.0                             Handelsname   
...            ...   ...                                     ...   
537919  741_sd.pdf   3.0                                       /   
537920  741_sd.pdf   3.0                                      m³   
537921  741_sd.pdf   3.0                                  *Dampf   
537922  741_sd.pdf   3.0                                     und   
537923  741_sd.pdf   3.0                                 Aerosol   
537924  741_sd.pdf   3.0                                109-16-0   
537925  741_sd.pdf   3.0  2,2´-Ethylendioxydiethyldimethacrylate   
537

In [ ]:
feature_selection_w = set_feature_rng_w(data)
train, test = prepare_data(data, 527)
start_training(feature_selection_w, ['label_group', 'chem', 'date'])

In [12]:
'''
# Feature Groups
#feature_sel = [('Paper','word.is.lower', 'word.is.stop'), ('Own','word.is.title','is.page.3'), ('Wordembedding', '0', '299'), ('Paper+Own','word.is.lower', 'is.page.3'), ('Own+Wordembedding', 'word.is.title', '299'), ('Paper+Own+Wordembedding', 'word.is.lower', '299')]


for feat in feature_sel:
    print ('***Features:' + feat[0] + '***')
    for lab in label:
        print ('***Label:' + lab + '***')
        # Separate random_data training/test split in features and labels
        x_train = train.loc[:, feat[1]:feat[2]]
        x_test = test.loc[:, feat[1]:feat[2]]
        y_train = train.loc[:, lab]
        y_test = test.loc[:, lab]

        # Balance classes
        #smote = SMOTE('minority')
        #x_sm, y_sm = smote.fit_sample(x_train, y_train)
        #x_sm.shape, y_sm.shape

        # training
        start = timer()
        clf = RandomForestClassifier(verbose=1)
        clf.fit (x_train, y_train)
        #clf.fit(x_sm, y_sm)
        y_pred = clf.predict(x_test)
        end = timer()
        print('Seconds for training:', end - start)

        # scores
        print(classification_report(y_pred=y_pred, y_true=y_test))

        # Output a pickle file for the model
        joblib.dump(clf, './models/'feat[0] + '_' + lab + '.pkl')
'''

"\n# Feature Groups\n#feature_sel = [('Paper','word.is.lower', 'word.is.stop'), ('Own','word.is.title','is.page.3'), ('Wordembedding', '0', '299'), ('Paper+Own','word.is.lower', 'is.page.3'), ('Own+Wordembedding', 'word.is.title', '299'), ('Paper+Own+Wordembedding', 'word.is.lower', '299')]\n\n\nfor feat in feature_sel:\n    print ('***Features:' + feat[0] + '***')\n    for lab in label:\n        print ('***Label:' + lab + '***')\n        # Separate random_data training/test split in features and labels\n        x_train = train.loc[:, feat[1]:feat[2]]\n        x_test = test.loc[:, feat[1]:feat[2]]\n        y_train = train.loc[:, lab]\n        y_test = test.loc[:, lab]\n\n        # Balance classes\n        #smote = SMOTE('minority')\n        #x_sm, y_sm = smote.fit_sample(x_train, y_train)\n        #x_sm.shape, y_sm.shape\n\n        # training\n        start = timer()\n        clf = RandomForestClassifier(verbose=1)\n        clf.fit (x_train, y_train)\n        #clf.fit(x_sm, y_sm)\n    